## Photometry

This section gives a quick summary of how photometric calibration can be done in Astro-WISE.

### Deriving zeropoint and extinction

Photometric calibration in Astro-WISE is done by comparing the counts in standard stars on images to their magnitudes as listed in a reference catalog of standard stars. The final result is a PhotometricParameters object which stores the zeropoint and extinction. This object can then be used to photometrically calibrate your ReducedScienceFrames.

Lets again consider the OmegaCAM data used in previous exercises. It was observed the night of 31 May 2012, using the r filter. A Landolt standard star field, SA113, was observed that night. ReducedScienceFrames already exist in the database for that standard field exposure:

In [ ]:
context.set_project('TUTORIAL')
context.set_privileges(1)
print(context.get_current_project())

In [ ]:
q = ReducedScienceFrame.template.start == dateutil.parser.parse('2012-06-01T09:38:56')
len(q)

Lets again only look at CCD\#65:

In [ ]:
q = q & (ReducedScienceFrame.chip.name == 'ESO_CCD_#65')

Create a Photometric Source Catalog, a PhotSrcCatalog object, which crossmatches standard stars listed in a standard star catalog, known as a Photometric Reference Catalog, (a PhotRefCatalog object) with stars on the ReducedScienceFrame observation. An example command from the awe-prompt using a standard recipe is:

In [ ]:
filenames = [red.filename for red in q]

In [ ]:
task = PhotcatTask(instrument='OMEGACAM', red_filenames=filenames, transform=1, inspect=1, commit=1)
task.execute()

  - 'red\_filenames' is a list of the filenames of the ReducedScienceFrames of the standard star observations.
  - transform=1 ensures that differences between the passbands of the instrument and the standard photometric system are accounted for
  - inspect=1 means a plot will be created to inspect the resulting crossmatch (default inspect=0)
  - commit=1 ensures the result is saved in the database (default commit=0). 

The above command uses default settings for process parameters such as the standard stars to use and the configuration of the source extraction algorithm.

Create a Photometric Parameters Catalog, a PhotometricParameters object, which contains photometric parameters, such as zeropoint and exintction. An example command from the awe-prompt using a standard recipe is:

In [ ]:
task = PhotomTask(instrument='OMEGACAM', red_filenames=filenames,
                  pars={'PhotometricParameters.process_params.SIGCLIP_LEVEL': 3.5}, inspect=1, commit=1)
task.execute()

where ``red_filenames``, ``inspect`` and ``commit`` have the same meaning as for the Photometric Source Catalog. The process parameter for sigma clipping was increased; it removed individual standard star measurements which differ by more than 3.5 standard deviations from the median from the calculation of the zeropoint. The above command uses a default atmospheric extinction correction.
After following these steps ReducedScienceFrames which contain your scientific targets can be photometrically calibrated using the PhotometricParameters object.

Have a look at the inspect figure that was stored on the dataserver, e.g.:

In [ ]:
photoms = PhotometricParameters.photcat.frame.filename == filenames[0]
photom = photoms.user_only().max('creation_date')

In [ ]:
photom.inspect()

### Standard Star Catalog operations

To retrieve the standard star catalog from the database:

In [ ]:
refcat = PhotRefCatalog.get()
refcat.retrieve()

To explore its content, see the possibilities by typing:

In [ ]:
dir(refcat)

For example:

In [ ]:
mag_dict = refcat.get_dict_of_magnitudes('SloanR')

To overlay the content of the catalog over the frame of a standard field which we found in above exercises, retrieve the frame:

In [ ]:
q[0].retrieve()

Display it in ``skycat``:

In [ ]:
q[0].display(viewer='skycat')

You can also use ``ds9``:

In [ ]:
q[0].display(viewer='ds9')

Retrieve the standard star catalog in ``skycat`` format to local disk:

In [ ]:
refcat.make_skycat()

To find its filename:

In [ ]:
import glob
glob.glob('*scat')

In ``skycat`` (.scat file) use the *File* menu in skycat to load and display the image and the *Data-servers -> Local Catalogs* menu to load and overplot the standard catalog and overplot it.